<h1>Desafio Porto Seguro </h1>

https://www.kaggle.com/competitions/porto-seguro-data-challenge/data?select=train.csv

In [16]:
import pandas as pd 
import numpy as np 
import sympy as s 
import matplotlib.pyplot as plt 
import math

### read data in folder 

In [17]:
list_of_names = ['test','train']
dataframes_list = []
for i in range(len(list_of_names)):
    temp_df = pd.read_csv(list_of_names[i]+".csv")
    dataframes_list.append(temp_df)

In [18]:
temp_df

id  var1  var2  var3   var4  var5  var6  var7  var8  var9  ...  \
0          1    18    19  2853  29442  1386  2435    35  -999     3  ...   
1          8     4   110  1986  13684  7189  -999  -999    17     3  ...   
2         30     0    39  1019  10232   678   791    16  -999     3  ...   
3         43    20    39  1751   2689  8235  1042    13    10     1  ...   
4         46     7    44  2262  29428  6031   304    16  -999     3  ...   
...      ...   ...   ...   ...    ...   ...   ...   ...   ...   ...  ...   
14118  35295     4    39  2511  28766  1109  2094    31    24     3  ...   
14119  35296    19   129  1114   -999  6376  -999  -999    27  -999  ...   
14120  35301    27    44  1786  23761  9048   623    35    27     3  ...   
14121  35304     4    89   210  19593  3634  2453    35    27     1  ...   
14122  35306    21    53   568   4612  4982  1438    33    25     3  ...   

            var60       var61     var62     var63     var64       var65  \
0        0.311441    0.142303  0.056146  0.632694  0.024054    0.253356   
1     -999.000000 -999.000000  0.070991  0.773966  0.019315 -999.000000   
2     -999.000000    0.200814  0.051046  0.980827  0.018536 -999.000000   
3     -999.000000    0.352379  0.044301  0.951564  0.023684    0.363370   
4        0.021226    0.226161  0.059125  0.906155  0.020733 -999.000000   
...           ...         ...       ...       ...       ...         ...   
14118 -999.000000    0.069347  0.036178  0.869828  0.016160 -999.000000   
14119 -999.000000    0.295418  0.055899  0.921292  0.018293 -999.000000   
14120 -999.000000    0.203394  0.040697  0.930373  0.009440 -999.000000   
14121    0.070788    0.381038  0.100384  0.680121  0.041096 -999.000000   
14122 -999.000000    0.229701  0.125199  0.877901  0.046154 -999.000000   

           var66     var67     var68  y  
0        0.00603  0.132353  0.139706  1  
1     -999.00000  0.147059  0.106618  0  
2     -999.00000  0.382353  0.242647  0  
3        0.00201  0.147059  0.132353  0  
4     -999.00000  0.455882  0.132353  1  
...          ...       ...       ... ..  
14118 -999.00000  0.455882  0.147059  0  
14119 -999.00000  0.147059  0.198529  0  
14120 -999.00000  0.397059  0.158088  0  
14121 -999.00000  0.264706  0.128676  0  
14122 -999.00000  0.176471  0.128676  0  

[14123 rows x 70 columns]

In [4]:
pd.read_csv('metadata.csv')

Variavel cod          Variavel tipo
0            id    Qualitativo nominal
1          var1    Qualitativo nominal
2          var2    Qualitativo nominal
3          var3    Qualitativo nominal
4          var4    Qualitativo nominal
..          ...                    ...
65        var65  Quantitativo continua
66        var66  Quantitativo continua
67        var67  Quantitativo discreto
68        var68  Quantitativo discreto
69            y  Quantitativo discreto

[70 rows x 2 columns]

### Avliacao dos dados faltantes, formatos e caracteristicas do dataset 

In [5]:
# verrificando os tipos na minha base 
np.array(np.unique(temp_df.dtypes.tolist(),return_counts=True)).tolist()

[[dtype('int64'), dtype('float64')], [56, 14]]

In [6]:
# verrificando caso exista, a quantidade de nulos nas colunas 
temp_df.isna().any().value_counts()


False    70
dtype: int64

In [7]:
# com a conversao dos valores -999 para nulos conseguimos trabalhar melhor
df2 = temp_df.mask(temp_df <=-999.0)
df2.isna().any().value_counts()

False    44
True     26
dtype: int64

In [8]:
# selecionando as colunas numericas 
df2.select_dtypes(include=['float64','int64','bool']).any().value_counts()

True    70
dtype: int64

In [9]:
import markupsafe
from pandas_profiling import ProfileReport

p = ProfileReport(df2.iloc[:,1:],minimal=True)
p.to_notebook_iframe()

Summarize dataset:   0%|          | 0/5 [00:00<?, ?it/s]

Generate report structure:   0%|          | 0/1 [00:00<?, ?it/s]

Render HTML:   0%|          | 0/1 [00:00<?, ?it/s]

### Avaliacao e preenchimento dos dados faltantes

Nesse caso especifico temos MICE do tipo <b>Mcar</b> ausencia aletoria de dados sem relacao com outros valores

In [10]:
x = df2.iloc[:,1:].values
x

array([[1.80000000e+01, 1.90000000e+01, 2.85300000e+03, ...,
        1.32352941e-01, 1.39705882e-01, 1.00000000e+00],
       [4.00000000e+00, 1.10000000e+02, 1.98600000e+03, ...,
        1.47058824e-01, 1.06617647e-01, 0.00000000e+00],
       [0.00000000e+00, 3.90000000e+01, 1.01900000e+03, ...,
        3.82352941e-01, 2.42647059e-01, 0.00000000e+00],
       ...,
       [2.70000000e+01, 4.40000000e+01, 1.78600000e+03, ...,
        3.97058824e-01, 1.58088235e-01, 0.00000000e+00],
       [4.00000000e+00, 8.90000000e+01, 2.10000000e+02, ...,
        2.64705882e-01, 1.28676471e-01, 0.00000000e+00],
       [2.10000000e+01, 5.30000000e+01, 5.68000000e+02, ...,
        1.76470588e-01, 1.28676471e-01, 0.00000000e+00]])

In [19]:
from sklearn.experimental import enable_iterative_imputer # modulo ainda em experimento
from sklearn.impute import IterativeImputer
from sklearn.tree import DecisionTreeRegressor as estim

imp2 = IterativeImputer(estimator=estim(),max_iter=10) # usando arvore de regressao pois arvores nao sofrem com ruidos, outiliers
imp2.fit(x)
x_imp = imp2.transform(x)
x_imp

c:\Users\Familia\anaconda3\lib\site-packages\sklearn\impute\_iterative.py:700: ConvergenceWarning: [IterativeImputer] Early stopping criterion not reached.
  warnings.warn(


array([[1.80000000e+01, 1.90000000e+01, 2.85300000e+03, ...,
        1.32352941e-01, 1.39705882e-01, 1.00000000e+00],
       [4.00000000e+00, 1.10000000e+02, 1.98600000e+03, ...,
        1.47058824e-01, 1.06617647e-01, 0.00000000e+00],
       [0.00000000e+00, 3.90000000e+01, 1.01900000e+03, ...,
        3.82352941e-01, 2.42647059e-01, 0.00000000e+00],
       ...,
       [2.70000000e+01, 4.40000000e+01, 1.78600000e+03, ...,
        3.97058824e-01, 1.58088235e-01, 0.00000000e+00],
       [4.00000000e+00, 8.90000000e+01, 2.10000000e+02, ...,
        2.64705882e-01, 1.28676471e-01, 0.00000000e+00],
       [2.10000000e+01, 5.30000000e+01, 5.68000000e+02, ...,
        1.76470588e-01, 1.28676471e-01, 0.00000000e+00]])

In [20]:
from scipy.stats import kurtosis
	
kurtosis(x_imp,fisher = False)>3

array([False, False, False, False, False, False, False, False, False,
        True, False, False, False, False, False, False, False,  True,
       False, False, False, False, False, False, False, False, False,
       False,  True, False,  True, False, False, False, False, False,
        True,  True,  True, False,  True,  True,  True,  True,  True,
        True,  True,  True, False,  True,  True, False,  True, False,
        True, False, False,  True,  True,  True,  True,  True,  True,
        True, False,  True,  True,  True,  True])

Detecatar os outiliers e tratatmento 

In [22]:
from pyod.models.knn import KNN

# muitas features incapaz de plotar todas, preciso analisar de forma geral meu conjunto 
detect = KNN()
detect.fit(x_imp)

KNN(algorithm='auto', contamination=0.1, leaf_size=30, method='largest',
  metric='minkowski', metric_params=None, n_jobs=1, n_neighbors=5, p=2,
  radius=1.0)

In [23]:
pred = detect.labels_
np.array(np.unique(pred,return_counts=True)).tolist()

[[0, 1], [12710, 1413]]

In [24]:
# valores que sao outliers 

detect.decision_scores_.tolist()

[2266.687367345416,
 1962.102612592089,
 1251.0685963528117,
 1320.2921454276711,
 2866.6191846596175,
 2642.5144014546454,
 3363.425926594651,
 1434.0442630080383,
 3405.715355816839,
 1027.8579185208423,
 1672.5769397442564,
 2109.2263902804584,
 2084.89690826833,
 1703.9469563491107,
 2105.794689358853,
 2509.1509900941287,
 1166.533556933361,
 1245.2254350790186,
 1390.0551209197954,
 1644.5078405954303,
 1953.2883368954108,
 1510.5618867976282,
 1184.4980568429435,
 3403.47647687404,
 2760.9112691580954,
 1944.7716180501175,
 2247.708766343412,
 2848.733250900374,
 2184.43022745755,
 1515.928968181794,
 2391.242898455203,
 1756.682590809257,
 1284.8625377847543,
 2161.306587161851,
 2122.4773986257965,
 2065.199613581819,
 1759.2159194462054,
 2473.766982319964,
 1110.7520384084282,
 1330.111797454657,
 1784.5613309579396,
 1836.6492288544619,
 2368.118639532414,
 2560.4164615814516,
 1338.1997940255637,
 1971.8920801822514,
 704.3088400813834,
 1184.4924003085848,
 1847.295402053

In [25]:
outliers =[] 
for i in range(len(pred)):
    if pred[i]==1:
        outliers.append(i)



In [26]:
# registros que sao outliers
df2.iloc[outliers,:]

id  var1   var2    var3     var4   var5    var6  var7  var8  var9  \
6         69     5   89.0  1906.0  28845.0   9676    64.0  35.0  27.0   3.0   
8         97     4   44.0   539.0  31622.0     50  2969.0  27.0  20.0   3.0   
23       239     7   53.0   740.0  30837.0   4136   482.0  35.0  27.0   1.0   
49       460    18  126.0  3265.0  32231.0    580   304.0  16.0  12.0   3.0   
87       800    18   53.0   722.0  25543.0   1109   820.0  35.0  27.0   2.0   
...      ...   ...    ...     ...      ...    ...     ...   ...   ...   ...   
14075  35155    19  129.0  3530.0  14221.0   6068  2277.0  27.0  20.0   3.0   
14079  35163     4  110.0  2789.0  24887.0  11096   872.0  35.0  27.0   3.0   
14087  35188     4   44.0   744.0  24247.0   6060  2941.0  12.0   9.0   1.0   
14091  35208    18  126.0  3375.0   5112.0   9544  2277.0  27.0  20.0   3.0   
14102  35236     6  126.0  1519.0  17763.0    149  2779.0  27.0  20.0   3.0   

       ...     var60     var61     var62     var63     var64     var65  \
6      ...       NaN  0.145790  0.035340  0.867810  0.014831       NaN   
8      ...  0.160714  0.252895  0.050784  0.857719  0.015547       NaN   
23     ...  0.111476  0.226335  0.235670  0.805247  0.079866  0.830890   
49     ...  0.355418  0.288580  0.137774  0.904137  0.017820       NaN   
87     ...  0.016039  0.246754  0.135974  0.825429  0.022662       NaN   
...    ...       ...       ...       ...       ...       ...       ...   
14075  ...  0.030104  0.315079  0.085140  0.956609  0.017744  0.155840   
14079  ...  0.096554  0.174205  0.089295  0.915237  0.029330       NaN   
14087  ...  0.147038  0.186764  0.074098  0.774975  0.019404       NaN   
14091  ...  0.107185  0.438865  0.329317  0.650858  0.090546  0.545595   
14102  ...  0.365521  0.242497  0.032749  0.956609  0.019967       NaN   

          var66     var67     var68  y  
6           NaN  0.514706  0.224265  0  
8           NaN  0.220588  0.143382  0  
23     0.004020  0.044118  0.187500  1  
49          NaN  0.044118  0.264706  1  
87          NaN  0.044118  0.176471  0  
...         ...       ...       ... ..  
14075  0.003015  0.044118  0.202206  1  
14079       NaN  0.176471  0.253676  0  
14087       NaN  0.161765  0.242647  0  
14091  0.003015  0.073529  0.158088  0  
14102       NaN  0.250000  0.198529  0  

[1413 rows x 70 columns]

In [ ]:
 2        |  0.8959   |  18.78    |  0.4006  

In [31]:
np.exp.at

<function ufunc.at>